# Simulation of the historical inflows
In this Notebook we are going to generate the historical reservoir inflows using historical weather data. 

To simulate the inflow we will use the HBV rainfall-runoff model.
## 1. HBV rainfall-runoff model 
In this example, we will use the HBV rainfall-runoff model [(Bergström, 1992)](https://www.smhi.se/en/publications/the-hbv-model-its-structure-and-applications-1.83591). The version used here is a Python version of the script included in the [SAFE Toolbox](https://www.safetoolbox.info/) by F. Pianosi, F. Sarrazin and T. Wagener at Bristol University (2015). The HBV model is a lumped hydrological model, meaning that all the processes included in the model are spatially aggregated into “conceptual” representations at the catchment scale.   In brief, the structure, forcing inputs, parameters and output of the model are the following.
### 1.1 General structure
The model consists of four main modules/subroutines: 
1. **SM module**: for soil moisture (***SM***), actual evapotranspiration (***EA***) and recharge estimation (***R***)
2. **UZ module**: for upper zone runoff generation (***Q0*** = surface runoff + interflow) and percolation (***PERC*** = water flux from upper to lower zone) 
3. **LZ module**: for lower zone runoff generation (***Q1*** = baseflow)
4. **Routing module**: for runoff routing.

<left><img src="Images/HBV model structure.png" width = "800px"><left>

### 1.2 Forcing inputs

The forcing inputs of the model simulation are time series of observed precipitation (***P***) and estimated potential evapotranspiration (***E***) – these are the spatial averages of precipitation and evapotranspiration across the watershed area. Usually these time series are given at daily resolution, and this will be the case in our example too, but it is possible to use shorter time steps.

### 1.3 Model parameters:
In order to tailor the general model equations to the particular watershed under study, we need to specify the watershed surface area, and a number of other parameters that characterise the climate, geology, soil properties, etc. of that place. These parameters are: 


1. ***SSM0***    = initial soil moisture [mm]
2. ***SUZ0***    = initial Upper Zone storage [mm]
3. ***SLZ0***    = initial Lower Zone storage [mm]
4. ***BETA***    = Exponential parameter in soil routine [-]
5. ***LP***      = Limit for potential evapotranspiration [-]
6. ***FC***      = Maximum soil moisture content [mm] 
7. ***PERC***    = Maximum flux from Upper to Lower Zone [mm/day]
8. ***K0***      = Near surface flow coefficient
9. ***K1***      = Recession coefficient for the Upper Zone (ratio) [1/day]
10. ***K2***     = Recession coefficient for the Lower Zone (ratio) [1/day]
11. ***UZL***    = Near surface flow threshold [mm]
12. ***MAXBAS*** = Transfer function parameter [day]

### 1.4 Model outputs
For a given selection of the model parameters and forcing input time series, the model simulation returns time series of the following state and flux variables: 

1. ***EA***    = Actual Evapotranspiration [mm/day]
2. ***SM***    = Soil Moisture [mm]
3. ***R***     = Recharge (water flow from Soil to Upper Zone) [mm/day]
4. ***UZ***    = Upper Zone water content [mm]
5. ***LZ***    = Lower Zone water content [mm]
6. ***RL***    = Recharge to the Lower Zone [mm]
7. ***Q0***    = Water flow from Upper Zone [ML/day]
8. ***Q1***    = Water flow from Lower Zone [ML/day]
9. ***Qsim*** = Total water flow [ML/day]

#### Comments:

- The Capillary flux ($CFLUX$; from upper tank to soil moisture accounting module) is not considered


- The recharge from the soil to the upper zone is considered to be a faster process than evapotranspiration.


- The preferred path in the Upper Zone dynamics can be selected by the flag $Case$:
    >flag=1 → Preferred path is runoff 
    
    >flag=2 → Preferred path is percolation

To run the model we need to import some necessary libraries. **Only if iRONs is run locally**: since one required library, [plotly](https://plot.ly/), is not available on Anaconda by default, you must have installed it first. Help on how to install libraries is given here: [How to install libraries](../0%20-%20Tutorials/0.b%20-%20How%20to%20install%20libraries.ipynb). If iRONs is run on the cloud, e.g. on [Binder](https://mybinder.org/) or [Microsoft Azure Notebooks](https://notebooks.azure.com/), we do not need to install the libraries to import them. 

Once all the necessary libraries are installed locally or we are running iRONs on the cloud, we can import them with the following code:

In [1]:
import numpy as np
from datetime import datetime, timedelta
import ipywidgets as widgets
import plotly.graph_objs as go
# Sub-modules
from Submodules.HBV_model import HBV_model

## 2. Forcing inputs
We use historical weather data (precipitation and PET) to simulate the historical reservoir inflow from 1980 to 2015. 

If observed weather data is not available in our area of study, in the UK we can download historical daily climate data from the [CEH website](https://eip.ceh.ac.uk/apps/chess/). First we need to find your study are in the map and click on this location. Then we need to set the type of weather data we would like to download and the time period (the maximum length is 12 months). 

In this example, we have a single CSV file (Hist_clim_data.csv) with observed daily PET [mm], precipitation [mm] and mean temperature [degC] from 1980 to 2015.

In [4]:
Hist_data_file = 'Input data/Historical data/Hist_clim_data.csv'

skip_lines = 1 # The number of lines to skip at the beginning of the .csv file.
date_format = "%d/%m/%Y" # Format of the dates on the .csv files
dates_hist = np.genfromtxt(Hist_data_file, 
                      delimiter = ',',
                      skip_header=skip_lines,
                      dtype = object,
                      converters={0: lambda x: datetime.strptime(x.decode("utf-8"), "%d/%m/%Y")})[0:,0]
E_hist = np.genfromtxt(Hist_data_file, 
                    delimiter = ',',
                    skip_header=skip_lines)[0:,1] # in mm/day
P_hist = np.genfromtxt(Hist_data_file, 
                    delimiter = ',',
                    skip_header=skip_lines)[0:,2] # in mm/day 

Plotting the historical input data

In [5]:
# First we define the traces (layers of data)
trace_E_hist = go.Scatter(
    x = dates_hist,
    y = E_hist,
    name = "PET",
    line=dict(color='yellow', width=1),
    opacity=1)

trace_P_hist = go.Scatter(
    x = dates_hist,
    y = P_hist,
    name = "Precipitation",
    line=dict(color='blue', width=1),
    opacity=1)
# Then the figure layout
layout1 = go.Layout(title="Daily PET and precipitation",
                    xaxis=dict(showgrid=False,title = 'date'),
                    yaxis=dict(title = 'mm/day'),
                    width=900, 
                    height=400)
# Finally we plot figure using the pre-defined layout and traces
fig1 = go.Figure(data=[trace_P_hist,trace_E_hist],
               layout = layout1)
fig1

## 3. Model parameters 

In [ ]:
BETA   = 6.4    # exponential parameter in soil routine [-]
LP     = 0.8    # evapotranspiration limit [-]
FC     = max(np.finfo(float).eps,247.1)  # field capacity [mm] 
PERC   = 0.9    # maximum flux from Upper to Lower Zone [mm/Dt]
K0     = 1/3.9  # near surface flow coefficient (ratio) [1/Dt]  
K1     = 1/11.0 # upper Zone outflow coefficient (ratio) [1/Dt]  
K2     = 1/61.3 # lower Zone outflow coefficient (ratio) [1/Dt]  
UZL    = 27.3   # near surface flow threshold [mm]
MAXBAS = max(1,round(0.9))    # flow routing coefficient or Transfer function parameter [day]

param = [BETA, LP, FC, PERC, K0, K1, K2, UZL, MAXBAS]

case = 1 # preferred path in the Upper Zone dynamics

## 4. Warm-up
We run the model for one year (1980) to obtain the initial conditions of the simulation (1981-2015)

In [6]:
# Catchment area
catchment_area = 28.8 # km2
# We first set arbitrary values for the initial condtions
SSM0 = 200 # initial soil moisture [mm]
SUZ0 = 2.5 # initial Upper Zone storage [mm]
SLZ0 = 2.5 # initial Lower Zone storage [mm]
ini0 = [SSM0,SUZ0,SLZ0]
# We extract the weather data for the warm-up period
warmup_year_hist = 1980
indices_warmup_hist = [d.year == warmup_year_hist for d in dates_hist]
dates_warmup_hist = dates_hist[indices_warmup_hist]
E_warmup_hist = E_hist[indices_warmup_hist]
P_warmup_hist = P_hist[indices_warmup_hist]
# Then we run the model with the arbritrarly defined initial conditions and the calibrated parameters
[SM,UZ,LZ], [EA,R,RL,Q0,Q1,Q] = HBV_model(dates_warmup_hist, E_warmup_hist, P_warmup_hist, ini0, param, case)
ini_hist = [SM[-1],UZ[-1],LZ[-1]]

## 5. Simulation

In [7]:
indices_sim_hist = [d.year > warmup_year_hist for d in dates_hist]
dates_hist= dates_hist[indices_sim_hist]
E_hist = E_hist[indices_sim_hist]
P_hist = P_hist[indices_sim_hist]
[SM,UZ,LZ], [EA,R,RL,Q0,Q1,Q] = HBV_model(dates_hist, E_hist, P_hist, ini_hist, param, case)
I_hist = Q*catchment_area # flows Q (in mm) * area (km2) = I (in ML)

Plotting historical inflow

In [8]:
# First we define the traces (layers of data)
trace_I_hist = go.Scatter(
    x = dates_hist,
    y = I_hist,
    name = "historical inflow",
    line=dict(color='blue', width=1),
    opacity=1)
# Then the figure layout
layout2 = go.Layout(title="Daily reservoir inflow",
                    xaxis=dict(showgrid=False,
                               title = 'date'),
                    yaxis=dict(title = 'ML/day'),
                    width=900, 
                    height=400)
# Finally we plot figure using the pre-defined layout and traces
fig2 = go.Figure(data=[trace_I_hist],
               layout = layout2)
fig2

## 6. Save the resutls
Save the historical inflow simulation into a csv file

In [9]:
# First we need to transform the data that we want to save into strings
dates_hist_str = [dates_hist[i].strftime("%d/%m/%Y") for i in range(len(dates_hist))]
I_hist_str = [str(I_hist[i]) for i in range(len(I_hist))]
# Then we can save the data in string format in a csv file
np.savetxt('Results/Hist_inflow.csv',np.transpose([dates_hist_str, I_hist_str]), fmt = '%s', delimiter=',')

### References 

Bergström, S. (1992) The HBV model - its structure and applications. SMHI Reports RH, No. 4, Norrköping.